In [1]:
!git clone -b outputCoordinates https://github.com/tetunori/co-tracker
%cd co-tracker
!pip install -e .
!pip install opencv-python einops timm matplotlib moviepy flow_vis
!mkdir checkpoints
%cd checkpoints
!wget https://huggingface.co/facebook/cotracker/resolve/main/cotracker2.pth

Cloning into 'co-tracker'...
remote: Enumerating objects: 311, done.
remote: Counting objects: 100% (237/237), done.
remote: Compressing objects: 100% (152/152), done.
remote: Total 311 (delta 130), reused 156 (delta 83), pack-reused 74
Receiving objects: 100% (311/311), 55.32 MiB | 41.26 MiB/s, done.
Resolving deltas: 100% (148/148), done.
/home/studio-lab-user/sagemaker-studiolab-notebooks/co-tracker
Obtaining file:///home/studio-lab-user/sagemaker-studiolab-notebooks/co-tracker
  Running setup.py develop for cotracker
/home/studio-lab-user/sagemaker-studiolab-notebooks/co-tracker/checkpoints
--2024-05-11 09:36:03--  https://huggingface.co/facebook/cotracker/resolve/main/cotracker2.pth
Resolving huggingface.co (huggingface.co)... 3.160.5.76, 3.160.5.109, 3.160.5.25, ...
Connecting to huggingface.co (huggingface.co)|3.160.5.76|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://cdn-lfs.huggingface.co/repos/99/80/9980d78abf629546bc23aee3918967b68e7f1f

In [2]:
%cd ..
import os
import torch

from base64 import b64encode
from cotracker.utils.visualizer import Visualizer, read_video_from_path
from IPython.display import HTML

/home/studio-lab-user/sagemaker-studiolab-notebooks/co-tracker


In [3]:
video = read_video_from_path('./assets/out.mp4')
video = torch.from_numpy(video).permute(0, 3, 1, 2)[None].float()

In [ ]:
def show_video(video_path):
    video_file = open(video_path, "r+b").read()
    video_url = f"data:video/mp4;base64,{b64encode(video_file).decode()}"
    return HTML(f"""<video width="640" height="480" autoplay loop controls><source src="{video_url}"></video>""")
 
show_video("./assets/out.mp4")

In [5]:
from cotracker.predictor import CoTrackerPredictor

model = CoTrackerPredictor(
    checkpoint=os.path.join(
        './checkpoints/cotracker2.pth'
    )
)

In [6]:
if torch.cuda.is_available():
    model = model.cuda()
    video = video.cuda()

In [7]:
queries = torch.tensor([
    [0., 855., 216.],
    [0., 892., 247.],
    [0., 823., 273.],
    [0., 495., 374.],
    [0., 713., 310.],
    [0., 833., 400.],
    [0., 709., 409.],
    [0., 864., 314.],
    [0., 770., 285.],
])
if torch.cuda.is_available():
    queries = queries.cuda()

In [8]:
pred_tracks, pred_visibility = model(video, queries=queries[None])

/home/studio-lab-user/.conda/envs/default/lib/python3.9/site-packages/torch/nn/modules/conv.py:456: UserWarning: Plan failed with an OutOfMemoryError: CUDA out of memory. Tried to allocate 5.91 GiB. GPU  (Triggered internally at ../aten/src/ATen/native/cudnn/Conv_v8.cpp:924.)
  return F.conv2d(input, weight, bias, self.stride,


In [9]:
vis = Visualizer(
    save_dir='./videos',
    linewidth=4,
    # mode='cool',
#    tracks_leave_trace=-1
)
vis.visualize(
    video=video,
    tracks=pred_tracks,
    visibility=pred_visibility,
    filename='queries');

Video saved to ./videos/queries.mp4


In [10]:
show_video("./videos/queries.mp4")